- title: Job Interview Assistant
  1. Accept JD text/file & parse for key info
  2. Auto-generate interview questions
  3. Voice output for questions
  4. Convert spoken user replies to text
  5. Compare response vs. model answer
  6. Textual insights + scoring
  7. Voice or Text interview preference
  8. Save Q&A history, feedback, scores

Intro Generate Using Lamma

In [1]:
#   1. Accept JD text/file & parse for key info
#  2. Auto-generate interview questions

Intro = "Hi there my name is jd, i am here to help you ace you next interview, simply provide me with the job description and i will generate a list of interview questions for you to practice with.\n\n"

# user_input = input("Please provide the job description: ")

In [2]:
generate_questions = ""

### Question generator

llama 3.2:1b

In [3]:
# simple example
# from ollama import generate

# response = generate(
#     model="llama3.2:1b",
#     prompt="Translate this sentence to Urdu: I am not crazy."
# )

# # Print the response
# output = response['response']
# # print(len(output))
# print(output)

In [4]:
from ollama import generate

# Read job description from file
with open("jd.txt", "r") as file:
    job_description = file.read()

# Build the prompt for generating interview questions
prompt = f"""
You are a helpful assistant trained to generate interview questions based on job descriptions.

Task: Read the job description provided and generate relevant interview questions that assess a candidate’s fit for the role.

Instructions:
- Focus on the required skills, responsibilities, and qualifications.
- Include a mix of technical, behavioral, and situational questions.
- Aim for 4–7 questions total.

JOB DESCRIPTION:
{job_description}
"""

# Call Ollama using your custom or local LLaMA 3.2:1B model
response = generate(
    model="llama3.2:1b",  # Replace with your actual model name
    prompt=prompt
)

# Print the response
output = response['response']
print(output)


Based on the job description, I've generated relevant interview questions that assess a candidate's fit for the role. Here are 6 questions:

1. **What motivates you to work in a cleaning environment, and how do you ensure your personal hygiene and safety while on the job?**

This question assesses the candidate's motivation, attention to detail, and ability to prioritize their own well-being.

2. **Can you describe a time when you had to multitask and manage multiple responsibilities simultaneously? How did you handle the pressure?**

This behavioral question evaluates the candidate's ability to work independently and juggle different tasks under pressure.

3. **How would you handle a situation where you discover that there is an environmental hazard or safety issue in the facility? What steps would you take to report it and prevent harm to others?**

This situational question tests the candidate's problem-solving skills, attention to detail, and ability to prioritize concerns for safe

llama 3.2 instruct 

In [5]:
import subprocess

# Read job description from file
with open("jd.txt", "r") as file:
    job_description = file.read()

# Build prompt
prompt = f"""
You are a helpful assistant trained to generate interview questions based on job descriptions.

Task: Read the job description provided and generate relevant interview questions that assess a candidate’s fit for the role.

Instructions:
- Focus on the required skills, responsibilities, and qualifications.
- Include a mix of technical, behavioral, and situational questions.
- Aim for 2-4 questions total.

JOB DESCRIPTION:
{job_description}
"""

# Call Ollama using your custom or local LLaMA 3.2:1B model
response = generate(
    model="llama3:instruct",  # Replace with your actual model name
    prompt=prompt
)

# Print the response
output = response["response"]
# print the length of the output
print(len(output))
print(output) 

1483
Here are 4 interview questions that assess a candidate's fit for the Janitor role:

**Technical Question:**
What is your approach to ensuring all areas of the facility are clean and safe? Can you give me an example of a time when you identified and addressed a cleanliness issue in a previous workplace?

This question evaluates the candidate's attention to detail, ability to identify problems, and willingness to take initiative.

**Behavioral Question:**
Tell me about a time when you had to work independently without direct supervision. How did you manage your time and prioritize tasks? How do you stay motivated and focused on a task that may not be as engaging?

This question assesses the candidate's ability to work independently, manage their time effectively, and maintain motivation.

**Situational Question:**
Imagine you are cleaning a restroom and notice that the sink is clogged. What would you do? Would you try to fix it yourself or report the issue to maintenance?

This ques

- Voice output for questions
  - Use Kokoro for text to speech generation

In [6]:
# Intro = "Hi there my name is jd, i am here to help you prepare for your next job interview, simply provide me with the job description and i will generate a list of interview questions for you to practice with.\n\n"

In [7]:
from kokoro import KPipeline
from IPython.display import display, Audio
import soundfile as sf

output = output[:1000]
pipeline = KPipeline(lang_code='a', repo_id='hexgrad/Kokoro-82M')
generator = pipeline(text= output, voice='hm_omega') # hm_omega
for i, (gs, ps, audio) in enumerate(generator):
    # print(i, gs, ps)
    print(gs)
    display(Audio(data=audio, rate=24000, autoplay=i==0))
    # sf.write(f'{i}.wav', audio, 24000) #UNCOMMENT TO SAVE AUDIO FILES

c:\Users\Dell\anaconda3\envs\dl12\Lib\site-packages\torch\nn\modules\rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(
c:\Users\Dell\anaconda3\envs\dl12\Lib\site-packages\torch\nn\utils\weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


Here are 4 interview questions that assess a candidate's fit for the Janitor role:


**Technical Question:**


What is your approach to ensuring all areas of the facility are clean and safe? Can you give me an example of a time when you identified and addressed a cleanliness issue in a previous workplace?


This question evaluates the candidate's attention to detail, ability to identify problems, and willingness to take initiative.


...

Tell me about a time when you had to work independently without direct supervision. How did you manage your time and prioritize tasks? How do you stay motivated and focused on a task that may not be as engaging?


This question assesses the candidate's ability to work independently, manage their time effectively, and maintain motivation.


**Situational Question:**


Imagine you are cleaning a restroom and notice that the sink is clogged. What would you do? Would you try to fix it yourself or report the issue to maintenance?


This question


In [8]:
print(audio)
print(type(audio))

tensor([-9.5812e-07,  7.0900e-07, -5.3260e-07,  ..., -1.5857e-08,
         1.1076e-08, -2.4929e-07])
<class 'torch.Tensor'>


Take User Voice Input

In [11]:
import sounddevice as sd
from scipy.io.wavfile import write

# Settings
duration = 5  # seconds
sample_rate = 44100  # Hertz (CD-quality)
filename = 'output.wav'  # Output filename

print("Recording...")
user_input = sd.rec(int(duration * sample_rate), samplerate=sample_rate, channels=2, dtype='int16')
sd.wait()  # Wait until recording is finished
print("Recording complete.")

# Save the recorded audio
write(filename, sample_rate, user_input)
print(f"Audio saved as '{filename}'")


Recording...
Recording complete.
Audio saved as 'output.wav'


- Convert spoken user replies to text
  - Whisper

In [12]:
import whisper 
model = whisper.load_model("base") 

result = model.transcribe(audio="output.wav") 
print(result["text"])

 I'm just just doing this and I


- Compare response vs. model answer
 

- Textual insights + scoring


- Voice or Text interview preference


- Save Q&A history, feedback, scores